In [1]:
!pip install pycaret -q

     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 486.1/486.1 kB 7.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 302.2/302.2 kB 25.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 13.3/13.3 MB 69.4 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 160.5/160.5 kB 17.4 MB/s eta 0:00:00
  Preparing metadata (setup.py) ... done
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 258.0/258.0 kB 25.7 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 81.9/81.9 kB 9.2 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 21.6 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 79.9/79.9 MB 10.1 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 106.8/106.8 kB 12.0 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 80.7/80.7 kB 8.5 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 21.8/21.8 MB 53.9 MB/s eta 0:00:00
     ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 44.0/44.0 kB 

In [13]:
import pandas as pd
from pycaret.anomaly import *
import glob

In [14]:
import plotly.graph_objects as go
import plotly.express as px

def plot_predict(predict_df: pd.DataFrame, wtr: str, title: str, model_name: str):
  # plot value on y-axis and date on x-axis**
  fig = px.line(predict_df, x=predict_df.index, y=wtr, title=title, template = 'plotly_dark')

  # create list of outlier_dates**
  outlier_dates = predict_df[predict_df['Anomaly'] == 1].index

  # obtain y value of anomalies to plot**
  y_values = [predict_df.loc[i][wtr] for i in outlier_dates]

  fig.add_trace(go.Scatter(x=outlier_dates, y=y_values, mode = 'markers',
                  name = 'Anomaly',
                  marker=dict(color='red',size=10)))

  fig.show()
  # fig.write_html(f"/content/drive/MyDrive/RedLabHack/models_plot/{model_name}.html")
  fig.write_image(f"./{model_name}.png")


def prepare_data(data: pd.DataFrame, WITH_RESAMPLING = True):
  data['point'] = pd.to_datetime(data['point'])
  data.drop(['agent_version', 'labels', 'account_id', 'name', 'language', 'app_name', 'app_id', 'host', 'display_host'], axis=1, inplace=True)
  data.set_index('point', drop=True, inplace=True)
  data = data.groupby(level=0).sum()
  return data

In [21]:
new_data = pd.read_csv("/content/drive/MyDrive/RedLabHack/Dataset/filtered_data.csv")
new_data.head()

account_id   name                point  call_count  total_call_time  \
0           1  Apdex  2024-04-15 23:32:00      3896.0              1.5   
1           1  Apdex  2024-04-15 23:33:00      3916.5              0.0   
2           1  Apdex  2024-04-15 23:34:00      3991.5              0.5   
3           1  Apdex  2024-04-15 23:35:00      3990.5              0.5   
4           1  Apdex  2024-04-15 23:36:00      3912.5              2.0   

   total_exclusive_time  min_call_time  max_call_time  sum_of_squares  \
0                   0.5            0.5            0.5             0.0   
1                   1.0            0.5            0.5             0.0   
2                   1.0            0.5            0.5             0.0   
3                   0.5            0.5            0.5             0.0   
4                   1.0            0.5            0.5             0.0   

   instances language            app_name          app_id  scope  \
0        1.0     java  [GMonit] Collector  17592186045423    NaN   
1        1.0     java  [GMonit] Collector  17592186045423    NaN   
2        1.0     java  [GMonit] Collector  17592186045423    NaN   
3        1.0     java  [GMonit] Collector  17592186045423    NaN   
4        1.0     java  [GMonit] Collector  17592186045423    NaN   

           host  display_host  pid agent_version labels  
0  575f5ba20b4b  575f5ba20b4b    1         8.5.0     {}  
1  575f5ba20b4b  575f5ba20b4b    1         8.5.0     {}  
2  575f5ba20b4b  575f5ba20b4b    1         8.5.0     {}  
3  575f5ba20b4b  575f5ba20b4b    1         8.5.0     {}  
4  575f5ba20b4b  575f5ba20b4b    1         8.5.0     {}

In [22]:
data = prepare_data(new_data)
data.head()

call_count  total_call_time  total_exclusive_time  \
point                                                                    
2024-04-15 23:32:00      7794.0        31.599163             30.599163   
2024-04-15 23:33:00      7834.0        32.763374             33.763374   
2024-04-15 23:34:00      7984.5        35.276276             35.776276   
2024-04-15 23:35:00      7982.0        33.572502             33.572502   
2024-04-15 23:36:00      7828.0        44.575750             43.575750   

                     min_call_time  max_call_time  sum_of_squares  instances  \
point                                                                          
2024-04-15 23:32:00       0.500091       1.285708        2.049792        2.0   
2024-04-15 23:33:00       0.500103       4.322411        8.938635        2.0   
2024-04-15 23:34:00       0.500110       4.322411       16.068309        2.0   
2024-04-15 23:35:00       0.500110       4.159296        8.886156        2.0   
2024-04-15 23:36:00       0.500107      15.611876      135.348995        2.0   

                     scope  pid  
point                            
2024-04-15 23:32:00    0.0    2  
2024-04-15 23:33:00    0.0    2  
2024-04-15 23:34:00    0.0    2  
2024-04-15 23:35:00    0.0    2  
2024-04-15 23:36:00    0.0    2

In [16]:
all_models_path = glob.glob("/content/drive/MyDrive/RedLabHack/final_models/*")

In [17]:
model_results = dict()

In [18]:
for model_path in all_models_path:
  model_name = model_path.split("/")[-1].split(".")[0]
  loaded_model = load_model(model_path[:-4])
  pred = predict_model(loaded_model, data)
  model_results[model_name] = {
      "prediction": pred,
      "anomalies": pred[pred['Anomaly'] == 1]
  }

Transformation Pipeline and Model Successfully Loaded
Transformation Pipeline and Model Successfully Loaded
Transformation Pipeline and Model Successfully Loaded
Transformation Pipeline and Model Successfully Loaded


In [19]:
for model in list(model_results.keys()):
  res = model_results[model]
  prediction = res['prediction']
  anomalies = res['anomalies']
  plot_predict(prediction, "Anomaly_Score", f"Calls anomalies detection : {model}", model)

In [23]:
prediction

call_count  total_call_time  total_exclusive_time  \
point                                                                    
2024-04-15 23:32:00      7794.0        31.599163             30.599163   
2024-04-15 23:33:00      7834.0        32.763374             33.763374   
2024-04-15 23:34:00      7984.5        35.276276             35.776276   
2024-04-15 23:35:00      7982.0        33.572502             33.572502   
2024-04-15 23:36:00      7828.0        44.575748             43.575748   
...                         ...              ...                   ...   
2024-05-16 00:54:00      5115.0        27.668142             24.668142   
2024-05-16 00:55:00      4976.0        30.832607             27.832607   
2024-05-16 00:56:00      4849.0        35.625961             30.625961   
2024-05-16 00:57:00      4739.5        31.465870             27.965870   
2024-05-16 00:58:00      2338.5        10.327918              9.827918   

                     min_call_time  max_call_time  sum_of_squares  instances  \
point                                                                          
2024-04-15 23:32:00       0.500091       1.285708        2.049792        2.0   
2024-04-15 23:33:00       0.500103       4.322411        8.938635        2.0   
2024-04-15 23:34:00       0.500110       4.322411       16.068310        2.0   
2024-04-15 23:35:00       0.500110       4.159296        8.886155        2.0   
2024-04-15 23:36:00       0.500107      15.611876      135.348999        2.0   
...                            ...            ...             ...        ...   
2024-05-16 00:54:00       0.500105       6.620240       30.513096        2.0   
2024-05-16 00:55:00       0.500107       6.620240       37.006187        2.0   
2024-05-16 00:56:00       0.500107       6.281807       35.624043        2.0   
2024-05-16 00:57:00       0.500111       6.281807       30.665834        2.0   
2024-05-16 00:58:00       0.500114       2.509948        3.921972        1.0   

                     scope  pid  Anomaly  Anomaly_Score  
point                                                    
2024-04-15 23:32:00    0.0    2        0       4.594392  
2024-04-15 23:33:00    0.0    2        0       7.001225  
2024-04-15 23:34:00    0.0    2        0       4.800313  
2024-04-15 23:35:00    0.0    2        0       5.782002  
2024-04-15 23:36:00    0.0    2        0      70.891242  
...                    ...  ...      ...            ...  
2024-05-16 00:54:00    0.0    2        0       7.402132  
2024-05-16 00:55:00    0.0    2        0       5.431119  
2024-05-16 00:56:00    0.0    2        0       6.578734  
2024-05-16 00:57:00    0.0    2        0       6.151231  
2024-05-16 00:58:00    0.0    2        0   14212.387750  

[43272 rows x 11 columns]

In [24]:
prediction[prediction['Anomaly'] == 1]

call_count  total_call_time  total_exclusive_time  \
point                                                                    
2024-04-16 15:06:00      8704.5      1198.842529           1192.342529   
2024-04-16 15:07:00      9168.5       726.688171            717.188171   
2024-04-16 16:53:00      8355.0       909.000610            909.000610   
2024-04-16 16:54:00      8376.0       907.835632            906.835632   
2024-04-16 19:01:00      9024.0      1127.577881           1129.577881   
2024-04-16 19:02:00      8982.0      1079.988403           1078.988403   
2024-04-19 15:34:00     11203.5       938.580322            934.080322   
2024-04-19 15:35:00     11048.5      1649.995117           1650.495117   
2024-04-19 15:36:00     10319.5      1007.459351           1008.959351   
2024-04-19 19:33:00      8333.5       867.036926            858.536926   
2024-04-19 19:34:00      8509.5       971.331299            961.831299   
2024-04-20 10:34:00      7278.0       568.623047            563.623047   
2024-04-20 10:35:00      7467.5      1706.496826           1707.996826   
2024-04-20 10:36:00      7757.5      1437.075195           1442.575195   
2024-04-21 08:59:00      7749.5      1929.770508           1972.270508   
2024-04-21 09:00:00      7811.5      1337.338501           1359.838501   
2024-04-25 14:17:00      9240.5       877.219727            879.719727   
2024-04-25 14:18:00      9241.5       879.616821            883.116821   
2024-05-01 12:43:00      7363.0      1195.071167           1185.071167   
2024-05-01 12:44:00      7100.0      1181.762451           1171.762451   
2024-05-01 12:48:00      8171.0       691.303406            683.303406   
2024-05-01 12:49:00      8478.5      1316.854004           1306.354004   
2024-05-01 12:50:00      8377.0      1042.057373           1045.057373   
2024-05-01 12:51:00      8006.5      6361.770020           6388.270020   
2024-05-01 12:52:00      8098.5      7249.300293           7259.800293   
2024-05-01 12:53:00      8335.0      1333.549683           1314.549683   
2024-05-03 12:11:00      8306.5       977.445984            982.945984   
2024-05-03 12:36:00      8211.5      1065.365723           1061.865723   
2024-05-03 12:37:00      8252.0       889.502563            879.502563   
2024-05-03 12:40:00      8815.0      5827.152344           5844.152344   
2024-05-03 12:41:00      8808.0      5823.297852           5841.297852   
2024-05-04 08:24:00      6002.5       743.086914            748.586914   
2024-05-04 15:23:00      7885.0       832.846497            835.846497   
2024-05-04 15:24:00      8200.0       730.586243            734.586243   
2024-05-04 18:07:00      7962.5       827.716248            823.216248   
2024-05-04 18:08:00      7592.5       854.876709            853.376709   
2024-05-04 18:09:00      7613.5       726.179932            726.679932   
2024-05-04 18:10:00      7519.0       435.645874            430.645874   
2024-05-05 19:05:00      9177.0       748.136047            758.136047   
2024-05-05 19:06:00      9345.5       751.450500            762.950500   
2024-05-13 08:53:00      7780.0       312.473816            310.473816   
2024-05-13 08:54:00      7669.5       307.734039            307.234039   
2024-05-15 20:00:00      8465.5       986.074219            978.574219   
2024-05-15 20:01:00      8662.0       957.889709            959.889709   

                     min_call_time  max_call_time  sum_of_squares  instances  \
point                                                                          
2024-04-16 15:06:00       0.500096     330.700745    3.273406e+05        2.0   
2024-04-16 15:07:00       0.500088     330.700745    2.094237e+05        2.0   
2024-04-16 16:53:00       0.500085     276.943268    2.116441e+05        2.0   
2024-04-16 16:54:00       0.500085     276.943268    2.116396e+05        2.0   
2024-04-16 19:01:00       0.500108     272.393707    2.338324e+05        2.0   
2024-04-16 19:02:00       0.500121     272.393707    2.3